In [1]:
import pandas as pd
from datetime import datetime, timedelta
from script import processing
from script import api
from sqlalchemy import create_engine
import pytz
import numpy as np
import hvplot.pandas
db_url = 'sqlite:///instance/local.db'
engine = create_engine(db_url)


In [14]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [2]:
## initialize by batchprocess to have initial result 
p_profile = pd.read_pickle('./data/p_profile.pkl')
start_date = p_profile.date.min()
end_date = pd.to_datetime(datetime.now()-timedelta(days=7))
# collect data upto 7 days ago  
b_profile, error  = api.update_benchmark_profile(start_date, end_date)
p_stocks, error = api.get_stocks_price(p_profile, start_date, end_date)
b_stocks, error = api.get_stocks_price(b_profile, start_date, end_date)

FileNotFoundError: [Errno 2] No such file or directory: './data/p_profile.pkl'

In [13]:
# save result 
# p_profile.to_pickle('./data/p_profile.pkl')
# b_profile.to_pickle('./data/b_profile.pkl')
p_stocks.to_pickle('./data/p_stocks.pkl')
b_stocks.to_pickle('./data/b_stocks.pkl')


In [12]:
## batch processing 
calculated_p_stock = processing.get_processing_result_of_stocks_df(p_stocks, p_profile)
calculated_b_stock = processing.get_processing_result_of_stocks_df(b_stocks, b_profile)
p_eval_df = processing.get_portfolio_evaluation(calculated_p_stock, calculated_b_stock, p_profile)
sector_eval_df = processing.get_portfolio_sector_evaluation(calculated_p_stock, calculated_b_stock)
attribution_result_df = processing.calculate_total_attribution(calculated_p_stock, calculated_b_stock)
s_attribution_result_df = processing.calculate_total_attribution_by_sector(calculated_p_stock, calculated_b_stock)

/Users/lamonkey/Desktop/risk monitor/script/processing.py:262: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.fillna(0, inplace=True)
/Users/lamonkey/Desktop/risk monitor/script/processing.py:263: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['active_return'] = df.pct_p * \
/Users/lamonkey/Desktop/risk monitor/script/processing.py:266: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/s

In [15]:
## save result to db
with engine.connect() as connection:
    # all_stock_info.to_sql('all_stock_info', con=connection, if_exists='replace', index=False)
    calculated_b_stock.to_sql('calculated_b_stock', con=connection, if_exists='replace', index=False)
    calculated_p_stock.to_sql('calculated_p_stock', con=connection, if_exists='replace', index=False)
    p_eval_df.to_sql('p_eval_result', con=connection, if_exists='replace', index=False)
    sector_eval_df.to_sql('sector_eval_result', con=connection, if_exists='replace', index=False)
    attribution_result_df.to_sql('attribution_result', con=connection, if_exists='replace', index=False)
    s_attribution_result_df.to_sql('s_attribution_result', con=connection, if_exists='replace', index=False)

In [63]:
# load from sql
name_df_map = dict()
with engine.connect() as connection:
    for table in ['calculated_b_stock','calculated_p_stock','p_eval_result','sector_eval_result']:
        try:
            df = pd.read_sql_table(table, con=connection)
            name_df_map[table] = df
        except:
            pass
            # TODO load data from api and calculate result 
    

In [91]:
# load data upto now
# Get the current time in UTC
current_time = datetime.datetime.utcnow()
# Set the timezone to Beijing
beijing_timezone = pytz.timezone('Asia/Shanghai')
# Convert the current time to Beijing time
end_time = pd.to_datetime(current_time.astimezone(beijing_timezone).date())
start_time = name_df_map['p_eval_result'].date.max() + timedelta(days=1)

# get data up to today
b_profile, error  = api.update_benchmark_profile(start_time, end_time)
p_stocks, error = api.get_stocks_price(p_profile, start_time, end_time)
b_stocks, error = api.get_stocks_price(b_profile, start_time, end_time)

In [185]:
most_recent_df = name_df_map['calculated_p_stock'].groupby('ticker').last().reset_index()
concat_df = pd.concat([most_recent_df, p_stocks], axis=0, join='outer')
processing.get_processing_result_of_stocks_df(concat_df, p_profile)

ValueError: The truth value of a Series is ambiguous. Use a.empty, a.bool(), a.item(), a.any() or a.all().

In [182]:
most_recent_df = name_df_map['calculated_p_stock'].groupby('ticker').last().reset_index()

def get_last_values(row):
    ticker = row['ticker']
    if ticker in p_profile['ticker'].values:
        return p_profile.loc[p_profile['ticker'] == ticker, ['display_name', 'name', 'aggregate_sector']].iloc[-1]
    else:
        return pd.Series([np.nan, np.nan, np.nan], index=['display_name', 'name', 'aggregate_sector'])
# dispaly_name, name and aggregate_sector
p_stocks[['display_name', 'name', 'aggregate_sector']] = p_stocks.apply(get_last_values, axis=1)

# use the most recent result to resume calculation
concat_df = pd.concat([most_recent_df, p_stocks], axis=0, join='outer')

# pct
concat_df['pct'] = concat_df.groupby('ticker')['close'].pct_change()

# calculate not normalized previous weight and current weight
groups = concat_df.groupby('ticker')
for _, group in groups:
    cur_weight = np.nan
    for index, row in group.iterrows():
        if pd.notna(row['current_weight']):
            cur_weight = row['current_weight']
        else:
            concat_df.loc[index, 'previous_weight'] = cur_weight
            cur_weight = cur_weight * (1 + row['pct'])
            concat_df.loc[index, 'current_weight'] = cur_weight

# calculate normalized previous and current weight
concat_df['prev_w_in_p'] = concat_df['previous_weight'] / \
    concat_df.groupby('date')['previous_weight'].transform('sum')
concat_df['cur_w_in_p'] = concat_df['current_weight'] / \
    concat_df.groupby('date')['current_weight'].transform('sum')

# calculate previous weight in sector
concat_df['pre_w_in_sector'] = concat_df['prev_w_in_p'] / \
    concat_df.groupby(['date', 'aggregate_sector'])['prev_w_in_p'].transform('sum')

# calculate pct in sector
concat_df['sector_pct'] = concat_df['pct'] * concat_df['pre_w_in_sector']





# remove group with first date
min_date_group = concat_df.groupby('date')['date'].idxmin()
concat_df = concat_df.drop(min_date_group)

# merge back to calculated_stock
pd.concat([name_df_map['calculated_p_stock'],concat_df]).reset_index(drop=True)

# concat_df[concat_df.ticker == '002709.XSHE'][['date','pct','current_weight','previous_weight','prev_w_in_p','cur_w_in_p']]

date       ticker    open   close    high     low       volume  \
0    2021-01-05  600409.XSHG    9.23    9.57    9.66    9.08   82669289.0   
1    2021-01-05  300274.XSHE   76.03   76.45   80.20   75.27   51384827.0   
2    2021-01-05  002920.XSHE   85.44   87.25   87.95   84.07    3852674.0   
3    2021-01-05  002709.XSHE   32.54   33.89   34.22   31.39   59152352.0   
4    2021-01-05  603882.XSHG  125.25  124.64  128.31  121.68    6803710.0   
...         ...          ...     ...     ...     ...     ...          ...   
3609 2023-06-27  600415.XSHG    8.52    8.69    8.78    8.40  151396630.0   
3610 2023-06-28  600415.XSHG    8.60    8.63    8.68    8.37  103167271.0   
3611 2023-06-29  600415.XSHG    8.60    8.74    8.88    8.58  128969467.0   
3612 2023-06-30  600415.XSHG    8.74    8.53    8.77    8.48  103029932.0   
3613 2023-07-03  600415.XSHG    8.45    8.37    8.46    8.05  133732493.0   

             money display_name  name  ... portfolio_pct  prev_w_in_sectore  \
0     7.803391e+08         三友化工  SYHG  ...           NaN                NaN   
1     3.961995e+09         阳光电源  YGDY  ...           NaN                NaN   
2     3.322598e+08         德赛西威  DSXW  ...           NaN                NaN   
3     1.942406e+09         天赐材料  TCCL  ...           NaN                NaN   
4     8.458543e+08         金域医学  JYYX  ...           NaN                NaN   
...            ...          ...   ...  ...           ...                ...   
3609  1.305075e+09         小商品城  XSPC  ...           NaN                NaN   
3610  8.798186e+08         小商品城  XSPC  ...           NaN                NaN   
3611  1.125704e+09         小商品城  XSPC  ...           NaN                NaN   
3612  8.844883e+08         小商品城  XSPC  ...           NaN                NaN   
3613  1.108033e+09         小商品城  XSPC  ...           NaN                NaN   

      ini_w_in_sector  sector_pct  portfolio_return  cum_pct  return  \
0                 1.0         NaN               NaN      NaN     NaN   
1                 0.5         NaN               NaN      NaN     NaN   
2                 1.0         NaN               NaN      NaN     NaN   
3                 0.5         NaN               NaN      NaN     NaN   
4                 1.0         NaN               NaN      NaN     NaN   
...               ...         ...               ...      ...     ...   
3609              NaN    0.027187               NaN      NaN     NaN   
3610              NaN   -0.006904               NaN      NaN     NaN   
3611              NaN    0.012746               NaN      NaN     NaN   
3612              NaN   -0.024027               NaN      NaN     NaN   
3613              NaN   -0.018757               NaN      NaN     NaN   

      sector_return  cur_w_in_p  pre_w_in_sector  
0               NaN         NaN              NaN  
1               NaN         NaN              NaN  
2               NaN         NaN              NaN  
3               NaN         NaN              NaN  
4               NaN         NaN              NaN  
...             ...         ...              ...  
3609            NaN    0.301143              1.0  
3610            NaN    0.299958              1.0  
3611            NaN    0.301804              1.0  
3612            NaN    0.293612              1.0  
3613            NaN    0.286010              1.0  

[3614 rows x 27 columns]